# American Muscles Network Analysis
***
Freddie Zhang <br>
April. 10, 2019 <br>
***
### Introduction
I picked three brands of the most famous American Muscle cars: **Ford Mustang**, **Chevrolet Camaro**, and **Dodge Challenger** to do a network analysis of brand mentioned tweets.

In [1]:
import warnings
warnings.filterwarnings('ignore')
import os
import re
import sys
import csv
import json
import glob
import time
import nltk
import spacy
import en_core_web_sm
import tweepy 
from tweepy import OAuthHandler 
import shutil
wn = nltk.WordNetLemmatizer()
ps = nltk.PorterStemmer()
import string
import zipfile
import itertools
from zipfile import ZipFile
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
from nltk.stem import WordNetLemmatizer
wordnet_lemmatizer = WordNetLemmatizer()
from ratelimiter import RateLimiter
from birdy.twitter import AppClient, UserClient, TwitterRateLimitError
from textblob import TextBlob 

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/yozh2004/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/yozh2004/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /home/yozh2004/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


### Selecting Brands
**Ford Mustang**, **Chevrolet Camaro**, and **Dodge Challenger**

### Fetching Twitter Data
I used Twitter API, specifically the Search Endpoint, to retrieve Tweets that mention three American Muscle brands for the period of from March 31th to April 9th. All fetched tweets will be saved as JSON inside a zip file.

In [2]:
import json, os, sys, time
from zipfile import ZipFile
from birdy.twitter import AppClient, UserClient, TwitterRateLimitError
from ratelimiter import RateLimiter

"""
Credentials can be found by selecting the "Keys and tokens" tab for your
application selected from:

https://developer.twitter.com/en/apps/
"""
CONSUMER_KEY = 'e2THlQj0jyQa1qrLjfr6fBfrz'
CONSUMER_SECRET = '6Nm6WZHzE9ynXzUOHF9Y4T2U783tzaQqr5M91UUkeVK8fRDLDF'


OUTPUT_DIR = 'tweets'
MAX_TWEETS = 10000 # max results for a search
max_id = None
_client = None


def client(consumer_key=None, consumer_secret=None):
    global _client
    if consumer_key is None:
        consumer_key = CONSUMER_KEY
    if consumer_secret is None:
        consumer_secret = CONSUMER_SECRET
    if _client is None:
        _client = AppClient(consumer_key, consumer_secret)
        access_token = _client.get_access_token()
        _client = AppClient(consumer_key, consumer_secret, access_token)
    return _client


def limited(until):
    duration = int(round(until - time.time()))
    print('Rate limited, sleeping for {:d} seconds'.format(duration))


@RateLimiter(max_calls=440, period=60*15, callback=limited)
def fetch_tweets(query, consumer_key=None, consumer_secret=None):
    global max_id
    print(f'Fetching: "{query}" TO MAX ID: {max_id}')
    try:
        tweets = client(consumer_key, consumer_secret).api.search.tweets.get(
            q=query,
            count=100,
            max_id=max_id).data['statuses']
    except TwitterRateLimitError:
        sys.exit("You've reached your Twitter API rate limit. "\
            "Wait 15 minutes before trying again")
    try:
        id_ = min([tweet['id'] for tweet in tweets])
    except ValueError:
        return None
    if max_id is None or id_ <= max_id:
        max_id = id_ - 1
    return tweets


def initialize_max_id(file_list):
    global max_id
    for fn in file_list:
        n = int(fn.split('.')[0])
        if max_id is None or n < max_id:
            max_id = n - 1
    if max_id is not None:
        print('Found previously fetched tweets. Setting max_id to %d' % max_id)


def halt(_id):
    print('Reached historically fetched ID: %d' % _id)
    print('In order to re-fetch older tweets, ' \
        'remove tweets from the output directory or output zip file.')
    sys.exit('\n!!IMPORTANT: Tweets older than 7 days will not be re-fetched')


def search_twitter(query, consumer_key=None, consumer_secret=None,
            newtweets=False, dozip=True, verbose=False):
    output_dir = os.path.join(OUTPUT_DIR, '_'.join(query.split()))
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
    if dozip:
        fn = os.path.join(output_dir, '%s.zip' % '_'.join(query.split()))
        outzip = ZipFile(fn, 'a')
    if not newtweets:
        if dozip:
            file_list = [f for f in outzip.namelist() if f.endswith('.json')]
        else:
            file_list = [f for f in os.listdir(output_dir) if f.endswith('.json')]
        initialize_max_id(file_list)
    while True:
        try:
            tweets = fetch_tweets(
                query,
                consumer_key=consumer_key,
                consumer_secret=consumer_secret)
            if tweets is None:
                print('Search Completed')
                if dozip:
                    outzip.close()
                break
            for tweet in tweets:
                if verbose:
                    print(tweet['id'])
                fn = '%d.json' % tweet['id']
                if dozip:
                    if fn in (file_list):
                        outzip.close()
                        halt(tweet['id'])
                    else:
                        outzip.writestr(fn, json.dumps(tweet, indent=4))
                        file_list.append(fn)
                else:
                    path = os.path.join(output_dir, fn)
                    if fn in (file_list):
                        halt(tweet['id'])
                    else:
                        with open(path, 'w') as outfile:
                            json.dump(tweet, outfile, indent=4)
                        file_list.append(fn)
                if len(file_list) >= MAX_TWEETS:
                    if fn in (file_list):
                        outzip.close()
                    sys.exit('Reached maximum tweet limit of: %d' % MAX_TWEETS)
        except:
            if dozip:
                outzip.close()
            raise

In [3]:
# search_twitter("fordmustang OR ford mustang")
# search_twitter("chevroletcamaro OR chevrolet camaro")
# search_twitter("dodgechallenger OR dodge challenger")

### Twitter Mentions Graph
I create a valued, directed network graph that shows mentions from Twitter users that are most centrally related to the brand. This graph will also illustrate who mentions who on Twitter, and in what way those mentions flow. 

In [4]:
TMPDIR = 'AMs' # change to AMs

In [5]:
if not os.path.exists(TMPDIR):
    os.makedirs(TMPDIR)

In [6]:
tweetzipfiles = glob.glob('*.zip')

In [7]:
for tweetzipfile in tweetzipfiles:
    with zipfile.ZipFile(tweetzipfile, "r") as f:
        print('Unzipping to AMs directory: %s' % tweetzipfile)
        f.extractall(TMPDIR)

Unzipping to AMs directory: chevroletcamaro_OR_chevrolet_camaro.zip
Unzipping to AMs directory: dodgechallenger_OR_dodge_challenger.zip
Unzipping to AMs directory: fordmustang_OR_ford_mustang.zip


In [8]:
uniqueusers = {}
count = 0
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        count += 1
        if count % 1000 == 0:
            print(count)
        tweetjson = json.load(f)
        userwhotweeted = tweetjson['user']['screen_name']
        
        if userwhotweeted in uniqueusers:
            uniqueusers[userwhotweeted] += 1
        if userwhotweeted not in uniqueusers:
            uniqueusers[userwhotweeted] = 1

1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000


In [9]:
len(uniqueusers)

7955

In [10]:
userstoinclude = set()
usercount = 0
for auser in uniqueusers:
    if uniqueusers[auser] > 1:
        usercount += 1
        userstoinclude.add(auser)
        
print(len(userstoinclude))

1304


In [11]:
edgelist = open('AMs.edgelist.for.gephi.csv', 'w') # JSON later
csvwriter = csv.writer(edgelist)
header = ['Source', 'Target']
csvwriter.writerow(header)

15

In [12]:
print('Writing edge list')
count = 0
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        tweetjson = json.load(f)
        userwhotweeted = tweetjson['user']['screen_name']
        if userwhotweeted in userstoinclude:
            count += 1
            if count % 1000 == 0:
                print(count)
            
            users = tweetjson['entities']['user_mentions']
            if len(users) > 0:
                for auser in users:
                    screenname = auser['screen_name']
                    row = [userwhotweeted, screenname]
                    csvwriter.writerow(row)
edgelist.close()

Writing edge list
1000
2000
3000
4000
5000
6000


### Who are the Most Central Users?

![title](img/1.png)

From the graph shown above, I can see there is a cluster for Ford at the bottom right with green lines, another cluster for Dodge is at the top left with dark gray lines. Unfortunately, there is no obvious cluster for Chevrolet because Chevrolet is not a big fan of Twitter, its official Twitter account only twitted nine times in March. However, there is another group, at the bottom left with pink lines, represents people who love racing or race events. I checked some users' tweet and I found these people were so engaged with engines, modification, and fast cars. From an advertising or marketing perspective, people in this cluster are "pro users" of American Muscle category, they could be treated as bridgers who will always be interested in this field.

![title](img/1.2.png)

The most central users for Ford: `FerVillarig`, `motorpuntoes`, `FordMX`, `StangTV`, `Joeylogano`, `BaccaBossMC`, `FordSpain`, `WashAutoShow`, `Motor1com`, `CarBuzzcom`.

![title](img/1.3.png)

The most central users for Dodge : `ChallengerJoe`, `OfficialMOPAR`, `Mrvinlabyu01`, `samlittlejohn1`, `Houtexelmo`, `southmiamimopar`, `melange_music`, `FasterMachines`, `trackshaker`, `CARiD_com`.

![title](img/1.1.png)

### Who are the Most Important Bridgers?

The most important bridgers: `StewartHaasRcng`, `nutri_chomps`, `Brendan85240221`, `jonah_ylhainen`, `RCRracing`, `ChaseBriscoe`, `hbpRacing`, `ruckusnetworks`, `ARRaacing7CR`, `cityboy20racing`. These bridgers include professional users, like `StewartHaasRcng`, `hbpRacing` and `RCRracing`, and popular users, like  `nutri_chomps` and `ChaseBriscoe`. These accounts have a lot of things in common. They are either professional racers or racing fans. They tend to comment on muscle cars in their Tweets or retweet Tweets related to these brands.

### Semantic Network Graph
I created a semantic network analysis graph that will reveal what words are most commonly associated with each other, for each brand. 

In [13]:
punctuation = string.punctuation
stopwordsset = set(stopwords.words("english"))
stopwordsset.add("'s")

In [14]:
#Removing urls
def removeURL(text):
    result = re.sub(r"http\S+", "", text)
    return result

#Removing Emoji
def removeEmojify(text):
    result = text.encode('ascii', 'ignore').decode('ascii')
    return result

In [15]:
#Extracting contextual words from a sentence
def tokenize(text):
    #lower case
    text = text.lower()
    #split into individual words
    words = word_tokenize(text)
    return words

def stem(tokenizedtext):
    rootwords = []
    for aword in tokenizedtext:
        aword = ps.stem(aword)
        rootwords.append(aword)
    return rootwords

def stopWords(tokenizedtext):
    goodwords = []
    for aword in tokenizedtext:
        if aword not in stopwordsset:
            goodwords.append(aword)
    return goodwords

def lemmatizer(tokenizedtext):
    lemmawords = []
    for aword in tokenizedtext:
        aword = wn.lemmatize(aword)
        lemmawords.append(aword)
    return lemmawords

def removePunctuation(tokenizedtext):
    nopunctwords = []
    for aword in tokenizedtext:
        if aword not in punctuation:
            nopunctwords.append(aword)
    cleanedwords = []
    for aword in nopunctwords:
        aword = aword.translate(str.maketrans('', '', string.punctuation))
        cleanedwords.append(aword)
    return cleanedwords

In [16]:
uniquewords = {}
count = 0
for tweetzipfile in tweetzipfiles:
    with zipfile.ZipFile(tweetzipfile, "r") as f:
        print("Unzipping to tmp directory: %s" % tweetzipfile)
        f.extractall(TMPDIR)

Unzipping to tmp directory: chevroletcamaro_OR_chevrolet_camaro.zip
Unzipping to tmp directory: dodgechallenger_OR_dodge_challenger.zip
Unzipping to tmp directory: fordmustang_OR_ford_mustang.zip


In [17]:
#shutil.rmtree(TMPDIR)

In [18]:
#from time import sleep
uniquewords = {}
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        tweetjson = json.load(f)
        count += 1 
        if count % 1000 == 0:
            print(count)
        
        text = tweetjson['text']
        nourlstext = removeURL(text)
        noemojitext = removeEmojify(nourlstext)
        tokenizedtext = tokenize(noemojitext)
        nostopwordstext = stopWords(tokenizedtext)
        lemmatizedtext = lemmatizer(nostopwordstext)
        nopuncttext = removePunctuation(lemmatizedtext)
        print(nopuncttext)
       # sleep(1)
        for aword in nopuncttext:
            if aword in uniquewords:
                uniquewords[aword] += 1
            if aword not in uniquewords:
                uniquewords[aword] = 1

['fordmustangs', 'mustangaddict', 'fordmustang', 'fordmustangclassic']
['rt', 'driftpink', 'join', 'u', 'april', '11th', 'howard', 'university', 'school', 'business', 'patio', 'fun', 'immersive', 'experience', 'new', '2019', 'chevro']
['moment', 'anxiety', 'first', 'drive', 'year', 'pay', 'kind', 'drivewaydemons', 'dodge']
['rt', 'mustangsinblack', 'jamie', 'amp', 'boy', 'gt350h', 'mustang', 'fordmustang', 'mustangfanclub', 'mustanggt', 'mustanglovers', 'fordnation', 'stang']
['current', 'ford', 'mustang', 'run', 'least', '2026']
['new', 'ford', 'mustang', 'craptastic']
['go', 'big', 'go', 'mango', 'name', 'coat', 'gorgeous', '2019', 'dodge', 'challenger', 'gt', 'awd', 'view', 'detail']
['ohmysatana', 'chevrolet', 'camaro', 's']
['ford', 'electrified', 'vision', 'europe', 'includes', 'mustanginspired', 'suv', 'lot', 'hybrid']
['gregonabicycle', 'guthrieandres', 'johncshuster', 'lot', 'g', 'story', 'involves', 'time', 'square', 'impounded', 'ford', 'musta']
['2005', 'ford', 'mustang', '

['rt', 'davidkudla', 'detroit', 'ford', 'mustang', 'mustangpride', 'tslaq']
['want', 'see', 'next', 'ford', 'mustang']
['ford', 'mustang', 'gt', 'coupe', 'ao', '2016', 'click', '40700', 'km', '21980000']
['next', 'ford', 'mustang', 'know']
['markmelbin', 'nra', 'oh', 'wait', 'm']
['rt', 'topgearph', 'local', 'chevrolet', 'camaro', 'come', '20liter', 'turbo', 'engine', 'topgearph', 'chevroletph', 'mias2019', 'tgpmias2019']
['finished', 'platform', '15', 'legogroup', 'creator', 'ford', 'mustang', 'almost', '25y', 'played', 'lego']
['rt', 'svtcobras', 'throwbackthursday', 'today', 'feature', 'mustang', 'handsome', 'amp', 'legendary', '1967', 'shelby', 'gt500', '', 'ford', 'mustang', 'svtc']
['video', 'autobahn', 'ford', 'mustang', 'gt']
['rt', 'doctorow', '1967', 'ford', 'mustang']
['ford', 'file', 'trademark', 'application', 'mustang', 'mache']
['rt', 'tontonyams', 'fume', 'vous', 'voulez', 'tre', 'en', 'couple', 'sans', 'le', 'engagement', 'qui', 'vont', 'avec', 'moi', 'aussi', 'je', 'v

['welcome', 'navehtalor', 'glad', 'introduce', 'nascar', 'fan', 'new', 'elite2', 'driver', 'naveh', 'join']
['rt', 'bigduke47', 'taillighttuesday', 'woop', 'woop']
['mustangtopic', 'nice', 'ride', 'always', 'liked', 're', 'fast', 'reason', 'always', 'reminded']
['need', 'accessory', 'bring', 'muscle', 'challenger', 'offering', '15', 'mopar', 'accessory']
['', 'lightweight', 'faire', 'buy', 'nephew', 'into', 'car', 'real', 'deal', '', 'ford']
['watch', 'dodge', 'challenger', 'srt', 'demon', 'hit', '211mph']
['carbizkaia']
['played', 'son', 'mustang', 'ford', 'swervedriver', 'raise', 'creation']
['rt', 'dodge', 'experience', 'legendary', 'style', 'new', 'dodge', 'challenger']
['rt', 'teampenske', 'brad', 'keselowski', '2', 'millerlite', 'ford', 'mustang', 'ready', 'go', 'txmotorspeedway', 'send', 'u', 'cheer']
['comparison', 'dodge', 'challenger', 'hellcat', 'redeye', 'vs', 'ferrari', '812', 'superfast']
['ford', 'electrified', 'vision', 'europe', 'includes', 'mustanginspired', 'suv', 'l

['mustang', 'convertible', 'fordmustang']
['anyone', 'tell', 'dusted', 'nigga', 'driving', 'dodge', 'challenger', 'honda', 'sonata', '', '']
['great', 'share', 'mustang', 'friend', 'fordmustang', 'realfastdad', 're', 'happy', 'hear', 'buying', 'mustang', 'today']
['rt', 'kblock43', 'check', 'rad', 'recreation', 'ford', 'mustang', 'rtr', 'hoonicorn', 'v2', 'lachlan', 'cameron', 'put', 'together', 'completely', 'using']
['rt', 'karaelf', 'ekl', 'binali', 'yldrm', 'bey', 'kazanrsa', 'bu', 'tweeti', 'rt', 'yapp', 'hesabm', 'takip', 'eden', 'kiiye', 'birer', 'harika', 'kitap', 'bir', 'kiiye', 'model']
['rt', 'jwok714', 'shelbysunday']
['rt', 'thejslforce', 'kotse', 'pa', 'lng', 'ulam', 'na', 'ano', 'pa', 'kaya', 'yung', 'may', 'ari', 'abaddon', 'alterra', 'aston', 'martin', 'audi', 'a5', 'bmw', 'corvette', 'ford', 'everest', 'ranger', 'fo']
['rt', 'svtcobras', 'frontendfriday', 'vintage', 'mustang', 'beauty', 'purest', 'form', '', 'ford', 'mustang', 'svtcobra']
['1', 'honda', 'city', 'gm2',

['ford', 'readying', 'new', 'flavor', 'mustang', 'could', 'new', 'svo']
['rt', 'mecum', 'born', 'run', 'info', 'amp', 'photo', 'mecumhouston', 'houston', 'mecum', 'mecumauctions', 'wherethecarsare']
['sanchezcastejon']
['historyla', 'forduruapan', 'ppmaqueo']
['rt', 'rcrracing', 'news', 'tylerreddick', '2', 'chevrolet', 'camaro', 'graced', 'one', 'iconic', 'country', 'singer', 'time', 'weeke']
['victor20miles', 'buy', 'plane', 'ticket', 'drive', 'dodge', 'challenger']
['797hp', '2019', 'dodge', 'challenger', 'srt', 'hellcat', 'redeye', 'prof', 'power', 'never', 'get', 'old']
['rt', 'aricalmirola', 'rough', 'night', 'last', 'night', 'thankfully', 'support', 'everybody', '10', 'smithfieldbrand', 'prime', 'fresh']
['rt', 'dodge', 'experience', 'legendary', 'style', 'new', 'dodge', 'challenger']
['2018', 'dodge', 'challenger', 'hellcat', 'royal', 'chrysler']
['lorenzo99', 'alpinestars', 'redbull', 'boxrepsol', 'hrcmotogp']
['january', 'braxx', 'racing', 'announced', 'would', 'enter', '90',

...

['dobge', 'omni', 'beter', 'ford', 'mustang', '30', 'secons']
['charlotte1509', 'ford', 'mustang', 'een', 'nieuwe', 'rode', 'cabrio', 'voor', 'de', 'boodschappen']
['rt', 'fordmusclejp', 'fordmustang', 'owner', 'museum', 'scheduled', 'grand', 'opening', 'april', '17th', 'displayed', 'memorabilia']
[]
['impressive']
['rt', 'teampenske', 'discounttire', 'ford', 'mustang', 'sure', 'looking', 'nice', 'rooting', 'keselowski', '2', 'crew', 'today', 'na']
['rt', 'stewarthaasrcng', 'going', 'big', 'buck', 'bmsupdates', 'thanks', 'fourthplace', 'finish', 'txmotorspeedway', 'chasebriscoe5', 'qualif']
['rt', 'frankymostro', 'el', 'estilo', 'pistero', 'que', 'pisteador', 'eso', 'e', 'otra', 'cosa', 'de', 'este', 'challenger', '70', 'e', 'de', 'gratis', 'abajo', 'del', 'cofre', 'trae']
['barn', 'find', '1968', 'ford', 'mustang', 'shelby', 'gt500', 'auction', 'frozen', 'time']
['rt', 'usbodysource', 'checkout', 'ford', 'fordmustang', 'mustang', 'mustangnation', 'mustang50', 'fordmustang50', 'mustang

['rt', 'rcrracing', 'news', 'tylerreddick', '2', 'chevrolet', 'camaro', 'graced', 'one', 'iconic', 'country', 'singer', 'time', 'weeke']
['ford', 'electrified', 'vision', 'europe', 'includes', 'mustanginspired', 'suv', 'lot', 'hybrid']
['fierce', 'ford', 'friday', 'software', 'engineer', 'hightech', 'gt', 'speed', 'carshow']
['rt', 'greencarguide', 'ford', 'announces', 'massive', 'rollout', 'electrification', 'go', 'event', 'amsterdam', 'including', 'new', 'kuga', 'mild', 'hybrid']
['ford', 'mustang', 'side', 'accent', 'stripe', 'promotorstripes', 'autographics', 'motorsport', 'vinylstripes']
['ebay', '1965', 'mustang', '', '1965', 'ford', 'mustang', 'vintage', 'classic', 'collector', 'performance', 'muscle']
['sheeple101', 'geoffschuler', 'usernamecusfish', 'thejollypumpkin', 'kmerian', 'lilearthling369', 'robinenochs', 'boysek']
['rt', 'mainefinfan', 'ca', 'nt', 'get', 'enough', 'cobrakaiseries', 'season', '2', 'trailer', 'watched', 'like', '5', 'time', 'morning', 'ca', 'nt', 'wait',

['rt', 'karaelf', 'ekl', 'binali', 'yldrm', 'bey', 'kazanrsa', 'bu', 'tweeti', 'rt', 'yapp', 'hesabm', 'takip', 'eden', 'kiiye', 'birer', 'harika', 'kitap', 'bir', 'kiiye', 'model']
['movistarf1']
['step', 'aside', 'demon', 're', 'upping', 'anty', '', 'thought', 'new', '200k', 'dodge', 'challenger', 'ghoul', 'mopar']
['joelobeya', 'lucastalunge', 'ycjkbe', 'zmcmc', 'mlsage', 'bigsua06', 'kenmanix', 'pmaotela', 'pa', 'mal', '', 'tu', 'du', 'got', 'mais', 'je', 'p']
['chevrolet', 'camaro', 'zl1', '1le', 'may', 'manual', 'get', 'optional', 'automatic', 'transmiss']
['buy', 'car', 'ohio', 'coming', 'soon', 'check', '2011', 'chevrolet', 'camaro', '1lt']
['prosor1', 'ford', 'mustang']
['1997', 'mustang', 'base', '2dr', 'fastback', '1997', 'ford', 'mustang', 'svt', 'cobra', 'base', '2dr', 'fastback']
['1', 'killed', 'ford', 'mustang', 'flip', 'crash', 'southeast', 'houston', 'via', 'abc13houston']
['dodge', 'challenger', 'rt', 'classic', 'mopar', 'musclecar', 'challengeroftheday']
['rt', 'dan

['ford', 'readying', 'new', 'flavor', 'mustang', 'could', 'newsvo']
['wowzabid', 'member', '', 'winner', 'brand', 'new', 'ford', 'mustang', 'auction', '28032019', 'winning', 'bid', '000', 'ng']
['flow', 'corvette', 'ford', 'mustang']
['ryanwalkinshaw', 'damienwhite', 'belowthebonnet', 'mustang', 'better', 'engineered', 'race', 'car', 'ca']
['stefthepef', 'excited', 'announced', 'new', 'explorer', 'platform', 'rwd', 'based', 'thinking', 'new', 'taurus']
['rt', 'paniniamerica', 'paniniamerica', 'riding', 'shotgun', 'nascarxfinity', 'driver', 'graygaulding', 'weekend', 'bmsupdates', 'whodoyoucollect']
[]
['new', 'arrival', 'new', 'ford', 'mustang', 'v8', 'gt', 'glorious', 'red', 'arrived', 'aprilfools', 'rear', 'view']
['rt', 'mustangsinblack', 'jamie', 'amp', 'boy', 'gt350h', 'mustang', 'fordmustang', 'mustangfanclub', 'mustanggt', 'mustanglovers', 'fordnation', 'stang']
['automobile', 'identify', '1992', 'ford', 'mustang', 'look', 'like', '80', 'cop', 'car', 'one', 'po']
['nextgeneratio

['rt', 'teampenske', 'joeylogano', '22', 'shellracingus', 'ford', 'mustang', 'win', 'stage', 'one', 'txmotorspeedway', '5th', 'blaney', 'menardsraci']
['2020', 'ford', 'mustang', 'getting', 'entrylevel', 'performance', 'model']
['2004', 'ford', 'mustang', '155000', 'mile', '2500', '40th', 'year', 'anniversary', 'edition', 'available', 'tim', 'short', 'acura']
['djrtpfanpage', 'doesnt', 'matter', 'supercars', '888', 'slow', 'ford', 'mustang', 'keep', 'fighting', 'boy', 'go', 'ford']
['check', 'ford', 'mustang', 'gt', 'set', '20', 'vossenwheels', 'cv10', 'finished', 'satin', 'black', 'falkentire', '']
['elonmusk', 'russian', 'car', 'tesla', 'mustang', '', 'aviar', '', 'price', '474000', 'dollar', 'electr']
['fordrangelalba']
['forza', 'horizon', '4', '2018', 'ford', '88', 'mustang', 'rtr', 'glen', 'rannoch', 'hillside', 'sprint', 'lovecars', 'xboxone', 'forzahorizon4', 'ford']
['rt', 'instanttimedeal', '1968', 'camaro', 's', 'great', 'stance', 'electric', 'r', 'hideaway', '350ci', 'motor

In [19]:
wordstoinclude = set()
wordcount = 0
for aword in uniquewords:
    if uniquewords[aword] >25:
        wordcount += 1
        wordstoinclude.add(aword)

In [20]:
print(wordcount)

791


In [21]:
edgelist = open('AMs.semantic.edgelist.for.gephi.csv','w')
csvwriter = csv.writer(edgelist)

header = ['Source', 'Target', 'Type']
csvwriter.writerow(header)

print('Writing Edgelist List')

uniquewords = {}
count = 0
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        tweetjson = json.load(f)
        count += 1 
        if count % 1000 == 0:
            print(count)
        
        text = tweetjson['text']
        nourlstext = removeURL(text)
        noemojitext = removeEmojify(nourlstext)
        tokenizedtext = tokenize(noemojitext)
        nostopwordstext = stopWords(tokenizedtext)
        lemmatizedtext = lemmatizer(nostopwordstext)
        nopuncttext = removePunctuation(lemmatizedtext)
        
        goodwords = []
        for aword in nopuncttext:
            if aword in wordstoinclude:
                goodwords.append(aword.replace(',',''))
                
        allcombos = itertools.combinations(goodwords, 2)
        for acombo in allcombos:
            row = []
            for anode in acombo:
                row.append(anode)
            row.append('Undirected')
            csvwriter.writerow(row)
edgelist.close()

Writing Edgelist List
1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000


![title](img/2.png)

![title](img/2.1.png)

![title](img/2.2.png)

### What Word Clusters Does Each Brand Own?
Base on the fact that the most central nodes are the attributes that each brand owns mostly, attributes are most uniquely linked to **Ford Mustang** are `gt500`, `shelby`, `classic`, and `gt`. Attributes are most uniquely linked to **Chevrolet Camaro** are `corvette`, `v6`, and `zl1`. Finally, attributes are most uniquely linked to **Dodge Challenger** are `srt`, `hellcat`, `demon`, `rt` and `wheel`.

### What are the Most Important Bridging Words?
In general, the most important bridging words include `electric`, `hybird`, `speed`, `news`, `suv`, and `supercars`. 

Generally, the clusters of these three brands are messy, I will segment the tweets in the following sections by sentiment, influential, and preprocess parts of speech to see if the semantic graph could be improved.

### Tweets Segmentation: By Sentiment

In [22]:
uniquewords = {}
count = 0
for tweetzipfile in tweetzipfiles:
    with zipfile.ZipFile(tweetzipfile, "r") as f:
        print("Unzipping to tmp directory: %s" % tweetzipfile)
        f.extractall(TMPDIR)

Unzipping to tmp directory: chevroletcamaro_OR_chevrolet_camaro.zip
Unzipping to tmp directory: dodgechallenger_OR_dodge_challenger.zip
Unzipping to tmp directory: fordmustang_OR_ford_mustang.zip


In [23]:
def clean_tweet(tweet): 
        return ' '.join(re.sub("(@[A-Za-z0-9]+)|([^0-9A-Za-z \t])|(\w+:\/\/\S+)", " ", tweet).split())

In [24]:
def get_tweet_sentiment(tweet): 
        # create TextBlob object of passed tweet text 
        analysis = TextBlob(clean_tweet(tweet)) 
        # set sentiment 
        if analysis.sentiment.polarity > 0: 
            return 'positive'
        elif analysis.sentiment.polarity == 0: 
            return 'neutral'
        else: 
            return 'negative'

In [25]:
tweets = []
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        tweetjson = json.load(f)
        count += 1 
        
        parsed_tweet = {}
        parsed_tweet['text'] = tweetjson['text']
        parsed_tweet['sentiment'] = get_tweet_sentiment(tweetjson['text'])
        if tweetjson['retweet_count'] > 0:
            if parsed_tweet not in tweets:
                tweets.append(parsed_tweet) 
            else:
                tweets.append(parsed_tweet)

In [26]:
# picking positive tweets from tweets 
ptweets = [tweet for tweet in tweets if tweet['sentiment'] == 'positive'] 
print("Positive tweets percentage: {} %".format(100*len(ptweets)/len(tweets)))

Positive tweets percentage: 42.748349974614996 %


In [27]:
# picking negative tweets from tweets 
ntweets = [tweet for tweet in tweets if tweet['sentiment'] == 'negative'] 
# percentage of negative tweets 
print("Negative tweets percentage: {} %".format(100*len(ntweets)/len(tweets)))

Negative tweets percentage: 6.786258250126925 %


In [28]:
print("Neutral tweets percentage: {} %".format(100*(len(tweets) - len(ntweets) - len(ptweets))/len(tweets)))

Neutral tweets percentage: 50.465391775258084 %


In [29]:
edgelist = open('AMs.positive.edgelist.for.gephi.csv','w')
csvwriter = csv.writer(edgelist)

header = ['Source', 'Target', 'Type']
csvwriter.writerow(header)

print('Writing Edgelist List')

uniquewords = {}
for tweet in ptweets: 
    text = tweet['text']
    nourlstext = removeURL(text)
    noemojitext = removeEmojify(nourlstext)
    tokenizedtext = tokenize(noemojitext)
    nostopwordstext = stopWords(tokenizedtext)
    lemmatizedtext = lemmatizer(nostopwordstext)
    nopuncttext = removePunctuation(lemmatizedtext)
    
    goodwords = []
    for aword in nopuncttext:
        if aword in wordstoinclude:
            goodwords.append(aword.replace(',',''))
                
    allcombos = itertools.combinations(goodwords, 2)
    for acombo in allcombos:
        row = []
        for anode in acombo:
            row.append(anode)
        row.append('Undirected')
        csvwriter.writerow(row)
edgelist.close()

Writing Edgelist List


### Semantic Network Graph Segmented By Positive Sentiment

![title](img/3.png)

![title](img/3.1.png)

![title](img/3.2.png)

### What Word Clusters Does Each Brand Own?
Base on the fact that the most central nodes are the attributes that each brand owns mostly, attributes are most uniquely linked to **Ford Mustang** are `cobra`, `fordperformance`, `performance`, `full`, `2020`, `streetlegal`, `gt`, `ford`, `red`, `match`, `fastback`, `1969`, `shelby`, `svtcobra`, `svtcobras`, `1966`, `black`, `mustanginspired` and `gt500`. Attributes are most uniquely linked to **Chevrolet Camaro** are `weekend`, `mile`, `speed`, `muscle`, `2015` and `camaro`. Finally, attributes are most uniquely linked to **Dodge Challenger** are `srt`, `daveinthedesert`, `v8`, `musclecar`, `fun`, `hot` and `day`.

### What are the Most Important Bridging Words?
In general, the most important bridging words include `powerful`, `la`, `speed`, `engine`, `kblock43`, `race`, `mile` and `supercars`. 

### Semantic Network Graph Segmented By Positive Sentiment
The semantic network graph segmented by sentiment makes more sense. Clusters for three brands became more remarkable. The cluster of **Dodge Challenger** is on the left with pink lines. The cluster of **Chevrolet Camaro** is in the middle with blue lines. And the cluster of **Ford Mustang** is on the top with green lines. 

In [30]:
edgelist = open('AMs.negative.edgelist.for.gephi.csv','w')
csvwriter = csv.writer(edgelist)

header = ['Source', 'Target', 'Type']
csvwriter.writerow(header)

print('Writing Edgelist List')

uniquewords = {}
for tweet in ptweets: 
    text = tweet['text']
    nourlstext = removeURL(text)
    noemojitext = removeEmojify(nourlstext)
    tokenizedtext = tokenize(noemojitext)
    nostopwordstext = stopWords(tokenizedtext)
    lemmatizedtext = lemmatizer(nostopwordstext)
    nopuncttext = removePunctuation(lemmatizedtext)
    
    goodwords = []
    for aword in nopuncttext:
        if aword in wordstoinclude:
            goodwords.append(aword.replace(',',''))
                
    allcombos = itertools.combinations(goodwords, 2)
    for acombo in allcombos:
        row = []
        for anode in acombo:
            row.append(anode)
        row.append('Undirected')
        csvwriter.writerow(row)
edgelist.close()

Writing Edgelist List


### Semantic Network Graph Segmented By Negative Segmentation

![title](img/4.png)

![title](img/4.1.png)

![title](img/4.2.png)

### What Word Clusters Does Each Brand Own?
Base on the fact that the most central nodes are the attributes that each brand owns mostly, attributes are most uniquely linked to **Ford Mustang** are `cobra`, `fordperformance`, `shelby`, `take`, `powerful`, `streetlegal`, `model`, `mach`, `shelby`, `1970`, `svtcobras`, `svtcobra`, `coupe`, `original`, `full`, `mile`, `mustanginspired`, `fastback` ,and `gt500`. There is no significant clustter for **Dodge Challenger** and **Chevrolet Camaro** with negative sentiment.

### What are the Most Important Bridging Words?
Since there is only one significant cluster for **Ford Mustang**, I could not tell there are bridging words in this semantic graph.

### Semantic Network Graph Segmented By Negative Sentiment
The semantic network graph of negative sentiment doesn't provide enough information with Dodge Challenger and Chevrolet Camaro. Because of the lack of information, the semantic network fails to tell the commonalities of these brands. In general, clusters for Ford Mustang are remarkable. 

### Tweets Segmentation: By influential

In [31]:
influential_user = []
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        tweetjson = json.load(f)
        
        follower_tweet = {}
        follower_tweet['screen_name'] = tweetjson['user']['screen_name']
        follower_tweet['followers_count'] = tweetjson['user']['followers_count']
        if tweetjson['retweet_count'] > 0:
            if follower_tweet not in influential_user:
                influential_user.append(follower_tweet) 
            else:
                influential_user.append(parsed_tweet)

In [32]:
edgelist = open('popuser.edgelist.for.gephi.csv', 'w') # JSON later
csvwriter = csv.writer(edgelist)
header = ['Source', 'Target']
csvwriter.writerow(header)

15

In [33]:
print('Writing edge list')
count = 0
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        tweetjson = json.load(f)
        
        popuser = tweetjson['user']['screen_name']
        if tweetjson['user']['followers_count'] > 1500:
            if popuser in userstoinclude:
                users = tweetjson['entities']['user_mentions']
                if len(users) > 0:
                    for auser in users:
                        screenname = auser['screen_name']
                        row = [popuser, screenname]
                        csvwriter.writerow(row)
edgelist.close()

Writing edge list


![title](img/5.1.png)

The most central users for Dodge : `ChallengerJoe`, `TheOriginalCOTD`, `FasterMachines`, `MichianaCDJR`, `DODGERAM2500V10`, `1fatchance`, `melange_music`, `FLOldskool68`, `DaveDuricy`, `471Street`, `Moparunlimited`.

![title](img/5.2.png)

The most central users for Ford: `FordPerformance`, `austria63amy`, `BHCarClub`, `EHoleik`, `motorpuntoes`, `jwok_714`, `Motor1com`, `FoundV`, `MustangsUNLTD`, `CARandDRIVER`.

![title](img/5.3.png)

From the graphs shown above, I can see there are a few purple clusters for Ford Mustang in the middle of the graph. Also, I could find several green clusters for Dodge is at the top. Again, there is no obvious cluster for Chevrolet. There are two more big clusters at the bottom of the graph, which consists of official accounts of several famous racing clubs and professional news accounts. All these accounts are active users that post and retweet news about cars and races.

### Who are the Most Important Bridgers?

The most important bridgers: `BMSupdates`, `speedwaydigest`, `vdstaff58`, `mustang_marie`, `VicMan_CarEs`, `CARiD_com`, `EHoleik`, `KenLingenfelter`, `ForestSimple`, `USBodySource`. Since the official accounts of Ford Mustang, Chevrolet Camaro, and Dodge Challenger did not post too many tweets about their products, these professional users and feeds users provided primary and secondary sources about these brands.

### Preprocess Parts of Speech

In [34]:
nlp = en_core_web_sm.load()

In [35]:
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        tweetjson = json.load(f)
        count += 1 
        
        nlp_tweet = {}
        nlp_tweet['text'] = tweetjson['text']
        nlp_tweet['preprocess'] = nlp(tweetjson['text'])
        print(nlp_tweet)

{'text': '🏁🏎🙌🏼 #fordmustangs #mustang_addict #fordmustang #fordmustangclassic https://t.co/567KiDrzV7', 'preprocess': 🏁🏎🙌🏼 #fordmustangs #mustang_addict #fordmustang #fordmustangclassic https://t.co/567KiDrzV7}
{'text': 'RT @DriftPink: Join us April 11th on the Howard University School of Business patio for a fun immersive experience with the new 2019 Chevro…', 'preprocess': RT @DriftPink: Join us April 11th on the Howard University School of Business patio for a fun immersive experience with the new 2019 Chevro…}
{'text': 'That moment of anxiety before your first drive of the year. It pays to be kind!\n@DrivewayDemons @Dodge… https://t.co/rhzGHs4uKu', 'preprocess': That moment of anxiety before your first drive of the year. It pays to be kind!
@DrivewayDemons @Dodge… https://t.co/rhzGHs4uKu}
{'text': 'RT @mustangsinblack: Jamie &amp; the boys with our GT350H 😎 #mustang #fordmustang #mustangfanclub #mustanggt #mustanglovers #fordnation #stang…', 'preprocess': RT @mustangsinblack: Jamie

{'text': 'RT @AMiracleDetail: 2018 Ford Mustang GT - A Miracle Detailing - CQuartz Professional -  https://t.co/Gqt0kPLB2b Boynton Beach, Fl. Contact…', 'preprocess': RT @AMiracleDetail: 2018 Ford Mustang GT - A Miracle Detailing - CQuartz Professional -  https://t.co/Gqt0kPLB2b Boynton Beach, Fl. Contact…}
{'text': 'A continuous work in progress but man I still can’t get over the fact I own this car. Slowly nodding = spending all… https://t.co/QS8GwHHDzF', 'preprocess': A continuous work in progress but man I still can’t get over the fact I own this car. Slowly nodding = spending all… https://t.co/QS8GwHHDzF}
{'text': "RT @StewartHaasRcng: There's nothing better than a good looking Ford Mustang. Lucky for us, we've got quite a few of them! 😍 Which Bristol…", 'preprocess': RT @StewartHaasRcng: There's nothing better than a good looking Ford Mustang. Lucky for us, we've got quite a few of them! 😍 Which Bristol…}
{'text': 'Spent awhile at the End GONZAGA Store and caught this Ford F-100 

{'text': 'RT @permadiaktivis: Pilpres ini kayak disuruh milih Ford Mustang sama Bajay. yang satu diakui dunia, satu lagi dianggap polusi di banyak ne…', 'preprocess': RT @permadiaktivis: Pilpres ini kayak disuruh milih Ford Mustang sama Bajay. yang satu diakui dunia, satu lagi dianggap polusi di banyak ne…}
{'text': 'RT @wylsacom: Так, блэд. Говорят Ford во всю готовит к 2021 году Mustang… SUV… электрический. Это что вообще происходит? https://t.co/C6Las…', 'preprocess': RT @wylsacom: Так, блэд. Говорят Ford во всю готовит к 2021 году Mustang… SUV… электрический. Это что вообще происходит? https://t.co/C6Las…}
{'text': 'RT @MaSaTo_Design: CHEVROLET CAMARO MD Model\n\n※デザイン変更しました。 https://t.co/vtpaEZZ6tV', 'preprocess': RT @MaSaTo_Design: CHEVROLET CAMARO MD Model

※デザイン変更しました。 https://t.co/vtpaEZZ6tV}
{'text': 'RT @ANCM_Mx: Escudería Mustang Oriente apoyando a los que mas necesitan #ANCM #FordMustang https://t.co/P6r6HxhGhb', 'preprocess': RT @ANCM_Mx: Escudería Mustang Oriente apoyand

{'text': "RT @RCRracing: NEWS: @TylerReddick's No. 2 Chevrolet Camaro will be graced by one of the most iconic country singers of all time this weeke…", 'preprocess': RT @RCRracing: NEWS: @TylerReddick's No. 2 Chevrolet Camaro will be graced by one of the most iconic country singers of all time this weeke…}
{'text': '#ThinkPositive #BePositive #ThatsMyDodge #ChallengeroftheDay @Dodge @OfficialMOPAR @JEGSPerformance #Challenger #RT… https://t.co/63eB1i67JB', 'preprocess': #ThinkPositive #BePositive #ThatsMyDodge #ChallengeroftheDay @Dodge @OfficialMOPAR @JEGSPerformance #Challenger #RT… https://t.co/63eB1i67JB}
{'text': 'Car Thief Drives Ford Mustang Bullitt Right Through Showroom Doors https://t.co/MiOcRXMFNF', 'preprocess': Car Thief Drives Ford Mustang Bullitt Right Through Showroom Doors https://t.co/MiOcRXMFNF}
{'text': 'Ford’s ‘Mustang-inspired’ electric SUV will have a 370-mile\xa0range https://t.co/O9CQXhc0Wi https://t.co/kM5pyM0xUO', 'preprocess': Ford’s ‘Mustang-inspired’ elec

{'text': '1970 Ford Mustang Boss 302 #classicford #fordmustang #theboss #musclecar #carphotos #fbf #musclecarsdaily #mustang… https://t.co/oGKYjA4ymx', 'preprocess': 1970 Ford Mustang Boss 302 #classicford #fordmustang #theboss #musclecar #carphotos #fbf #musclecarsdaily #mustang… https://t.co/oGKYjA4ymx}
{'text': 'RT @MachavernRacing: In what turned into a 3-lap shoot-out to the checker, brought the No.77 @StevensSpring @LiquiMolyUSA @PrefixCompanies…', 'preprocess': RT @MachavernRacing: In what turned into a 3-lap shoot-out to the checker, brought the No.77 @StevensSpring @LiquiMolyUSA @PrefixCompanies…}
{'text': 'RT @DaveintheDesert: Are you ready for a #FridayFlashback? \n\nGang green...\n\n#MOPAR #MuscleCar #ClassicCar #Dodge #Challenger #MoparOrNoCar…', 'preprocess': RT @DaveintheDesert: Are you ready for a #FridayFlashback? 

Gang green...

#MOPAR #MuscleCar #ClassicCar #Dodge #Challenger #MoparOrNoCar…}
{'text': 'Ford Applies For "Mustang Mach-E" Trademark in the EU - https://t

...

{'text': 'RT @InstantTimeDeal: 1968 Camaro SS GREAT STANCE, ELECTRIC RS HIDEAWAYS, 350CI MOTOR, TH350 TRANS, GREAT COLOR COMBO https://t.co/y14RZmwpmO', 'preprocess': RT @InstantTimeDeal: 1968 Camaro SS GREAT STANCE, ELECTRIC RS HIDEAWAYS, 350CI MOTOR, TH350 TRANS, GREAT COLOR COMBO https://t.co/y14RZmwpmO}
{'text': 'Now live at BaT Auctions: 1964 1/2 Ford Mustang Hardtop Coupe 3-Speed https://t.co/OFiC2YoemF https://t.co/Zg3WlgCQGy', 'preprocess': Now live at BaT Auctions: 1964 1/2 Ford Mustang Hardtop Coupe 3-Speed https://t.co/OFiC2YoemF https://t.co/Zg3WlgCQGy}
{'text': 'RT @mustangsinblack: Jamie &amp; the boys with our GT350H 😎 #mustang #fordmustang #mustangfanclub #mustanggt #mustanglovers #fordnation #stang…', 'preprocess': RT @mustangsinblack: Jamie &amp; the boys with our GT350H 😎 #mustang #fordmustang #mustangfanclub #mustanggt #mustanglovers #fordnation #stang…}
{'text': 'RT @caralertsdaily: Ford Raptor to get Mustang Shelby GT500 engine in two years https://t.co/jLbibVJu4G

{'text': 'Check out Hot Wheels 2010 Super TREASURE HUNT$ ‘69 Ford Mustang Spectraflame Green 5SPRR’s https://t.co/qO0c7ex7BF @eBay', 'preprocess': Check out Hot Wheels 2010 Super TREASURE HUNT$ ‘69 Ford Mustang Spectraflame Green 5SPRR’s https://t.co/qO0c7ex7BF @eBay}
{'text': '@CarreraMujer @GemaHassenBey @belenjimenezalm https://t.co/XFR9pkofAW', 'preprocess': @CarreraMujer @GemaHassenBey @belenjimenezalm https://t.co/XFR9pkofAW}
{'text': '#MotorPasion https://t.co/DfBoCTZQ9M', 'preprocess': #MotorPasion https://t.co/DfBoCTZQ9M}
{'text': 'Lap 75 | @RyanJNewman P8, reports he’s loose in his @WyndhamRewards Ford Mustang.', 'preprocess': Lap 75 | @RyanJNewman P8, reports he’s loose in his @WyndhamRewards Ford Mustang.}
{'text': 'RT @PeterMDeLorenzo: THE BEST OF THE BEST.\n\nWatkins Glen, New York, August 10, 1969. Parnelli Jones in the No. 15 Bud Moore Engineering For…', 'preprocess': RT @PeterMDeLorenzo: THE BEST OF THE BEST.

Watkins Glen, New York, August 10, 1969. Parnelli Jones in 

{'text': 'RT @OKCPD: Last week this man stole a gold Ford Ranger w/ camper (Tag #HXZ629) from a dealership near NW 16th/MacArthur. He arrived in a wh…', 'preprocess': RT @OKCPD: Last week this man stole a gold Ford Ranger w/ camper (Tag #HXZ629) from a dealership near NW 16th/MacArthur. He arrived in a wh…}
{'text': 'In my Chevrolet Camaro, I have completed a 0.82 mile trip in 00:03 minutes. 0 sec over 112km. 0 sec over 120km. 0 s… https://t.co/wE0RcHLfOy', 'preprocess': In my Chevrolet Camaro, I have completed a 0.82 mile trip in 00:03 minutes. 0 sec over 112km. 0 sec over 120km. 0 s… https://t.co/wE0RcHLfOy}
{'text': 'Morgen mogen de witte muscle cars weer schitteren op een aantal bruiloften😁 #dodge #challenger #ford #mustang… https://t.co/98wRmphHtE', 'preprocess': Morgen mogen de witte muscle cars weer schitteren op een aantal bruiloften😁 #dodge #challenger #ford #mustang… https://t.co/98wRmphHtE}
{'text': 'Used 1968 Chevrolet Camaro for Sale in Indiana PA 15701 Hanksters https://t

{'text': 'RT @permadiaktivis: Pilpres ini kayak disuruh milih Ford Mustang sama Bajay. yang satu diakui dunia, satu lagi dianggap polusi di banyak ne…', 'preprocess': RT @permadiaktivis: Pilpres ini kayak disuruh milih Ford Mustang sama Bajay. yang satu diakui dunia, satu lagi dianggap polusi di banyak ne…}
{'text': '@movistar_F1 https://t.co/XFR9pkofAW', 'preprocess': @movistar_F1 https://t.co/XFR9pkofAW}
{'text': 'RT @GlenmarchCars: Chevrolet Camaro Z28 #77MM #Goodwood\n\n(Photo:@GlenmarchCars) https://t.co/c4NamRx0Re', 'preprocess': RT @GlenmarchCars: Chevrolet Camaro Z28 #77MM #Goodwood

(Photo:@GlenmarchCars) https://t.co/c4NamRx0Re}
{'text': "The No. 10 crew's working on that good looking #SHAZAM Ford Mustang! \n\n#SmithfieldRacing https://t.co/fK6mRrgVlR", 'preprocess': The No. 10 crew's working on that good looking #SHAZAM Ford Mustang! 

#SmithfieldRacing https://t.co/fK6mRrgVlR}
{'text': 'RT @SVT_Cobras: #ThrowbackThursday | Ⓜ️ Today’s feature Mustang is the handsome &amp; le

{'text': '@Bicknell_Loop @AndrewScheer Many boomers complained how the carbon tax affected their 7L V8 Ford Mustang.', 'preprocess': @Bicknell_Loop @AndrewScheer Many boomers complained how the carbon tax affected their 7L V8 Ford Mustang.}
{'text': 'RIP Tania Mallet, 77, Bond girl in GOLDFINGER (1964), her only movie role. First major female character in a #007 f… https://t.co/kaKvLM45O7', 'preprocess': RIP Tania Mallet, 77, Bond girl in GOLDFINGER (1964), her only movie role. First major female character in a #007 f… https://t.co/kaKvLM45O7}
{'text': 'Ford has applied to trademark "Mach-E". Those who buy the V8 will be angry, anyone else won\'t care #ford #mustang', 'preprocess': Ford has applied to trademark "Mach-E". Those who buy the V8 will be angry, anyone else won't care #ford #mustang}
{'text': 'RT @Barrett_Jackson: Begging to be let out of the stables! This 1969 @Ford Mustang Boss 302 is one of 1,628 produced in 1969 and is powered…', 'preprocess': RT @Barrett_Jackson: Beggin

In [36]:
doc = nlp(tweetjson['text'])

In [37]:
speech = []
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        tweetjson = json.load(f)
        doc = nlp(tweetjson['text'])
        preprocess = [chunk.text for chunk in doc.noun_chunks] + [token.lemma_ for token in doc if token.pos_ == "ADJ"]
        
        if tweetjson['retweet_count'] > 0:
            if preprocess not in speech:
                speech.append(preprocess) 
            else:
                speech.append(preprocess)

In [38]:
edgelist = open('speech.edgelist.for.gephi.csv','w')
csvwriter = csv.writer(edgelist)

header = ['Source', 'Target', 'Type']
csvwriter.writerow(header)

print('Writing Edgelist List')

uniquewords = {}
for fn in os.listdir(TMPDIR):
    fn = os.path.join(TMPDIR, fn)
    with open(fn) as f:
        tweetjson = json.load(f)
        doc = nlp(tweetjson['text'])
        
        preprocess = [chunk.text for chunk in doc.noun_chunks] + [token.lemma_ for token in doc if token.pos_ == "ADJ"]
        nostopwordstext = stopWords(preprocess)
        lemmatizedtext = lemmatizer(nostopwordstext)
        besttext = removePunctuation(lemmatizedtext)
        
        goodwords = []
        for aword in besttext:
            if aword in wordstoinclude:
                goodwords.append(aword.replace(',',''))
                
        allcombos = itertools.combinations(goodwords, 2)
        for acombo in allcombos:
            row = []
            for anode in acombo:
                row.append(anode)
            row.append('Undirected')
            csvwriter.writerow(row)
edgelist.close()

Writing Edgelist List


![title](img/6.png)

![title](img/6.1.png)

![title](img/6.2.png)

### What Word Clusters Does Each Brand Own?
Base on the fact that the most central nodes are the attributes that each brand owns mostly, attributes are most uniquely linked to **Ford Mustang** are `happy`, `great`, `available`, `favorite`, `nice`, and `new`. Attributes are most uniquely linked to **Dodge Challenger** are `low`, `powerful`, and `camaro`. Unfortuntaly, I couldn't find enough attributes telling the most unique words of **Chevrolet Camaro**.

### What are the Most Important Bridging Words?
In general, the most important bridging words include `american`, `beautiful`, `legendary`, and `musclecar`.

### Semantic Network Graph with Pre-processed Tweets
Performing text pre-processing omits years and some unnecessary verbs. However, I don't think this approach improves the semantic network since this network doesn't have enough attributes helping me identify the clusters of Chevrolet Camaro. 